# Ohio Wine - a look into the potential impact of Wine coming from Ohio
### This notebook will take data from the Ohio Data Portal, The Department of Agriculture in Ohio and the US government websites and see how the wine industry could be impacted after the toxic train derailment that happened in Easter Palestine OH, on February 3rd of 2023.

This analysis aims to highlight how the wine supply in Ohio - one of the major economic powerhouses -  may be affected after the recent train derailment in Palestine, OH with the release of large amounts of toxic chemicals.

The Sources I am using are:
1. https://agri.ohio.gov/
2. https://data.ohio.gov/wps/portal/gov/data/home
3. https://ustr.gov/map/state-benefits/oh
4. https://development.ohio.gov/static/business/export/2021-Ohio-Exports-Report.pdf
5. https://content.govdelivery.com/attachments/OHDOA/2023/01/20/file_attachments/2386278/2022%20Ohio%20Wine%20%20Grape%20Report%20Final%20Draft.pdf
6. https://findohiowines.ohio.gov/wps/wcm/connect/gov/cf0bb537-ebe6-469a-821f-31e56f617804/2022+Ohio+Wine++Grape+Report+Final+Draft.pdf?MOD=AJPERES&CONVERT_TO=url&CACHEID=ROOTWORKSPACE.Z18_K9I401S01H7F40QBNJU3SO1F56-cf0bb537-ebe6-469a-821f-31e56f617804-ongTWZm



In [39]:
# import necessary libraries
import pandas as pd
import numpy as np
from pathlib import Path 
import geoviews 
import hvplot.pandas
import urllib.request
import requests
import json

### Here is a geographical visualization of Palestine, OH: the location of the toxic train derailment

Ohio has a total of 223 locations listed on their Department of Agriculture website (6).
Ohio was the #7 major exporter of wines in 2022. Where CA and WA were 1 and 2 (6).
Welch's and J.M. Smuckers are major market players in the Ohio geographic area (6) and could have their products effected for the years to come. 

### Ohio Wineries
<img src="./images/Ohio_wine_map.png" width=500>

Map taken from the [findohiowines.ohio.gov](findohiowines.ohio.gov) website

In [58]:
# Grab a list of wineries from website using Beautiful Soup
from bs4 import BeautifulSoup
from lxml import etree 

# html website that contains list of wineries
url = 'https://findohiowines.ohio.gov/discover/find-ohio-wineries/find-ohio-wineries'

# get response
response = requests.get(url)

# set beautiful soup object with html5lib parser
soup = BeautifulSoup(response.content, 'html.parser')

# list to store wineries
wineries_titles = []
# list for winery locations
winery_locations = []


In [59]:
# Use soup object to query the webpage
main = soup.find_all('main', id='odx-main-content' )

In [83]:
print(str(soup))

<!DOCTYPE html>

<html class="no-js" lang="en">
<head>
<meta charset="utf-8"/>
<!-- rel=dynamic-content indicates an element that is replaced with the contents produced by the specified href. 
	 dyn-cs:* URIs are resolved using the WP DynamicContentSpotMappings resource environment provider. These values can
	 also be set using theme metadata if a theme is specified in the URI (e.g. @tl:oid:theme_unique_name). ODX v1.02 -->
<link href="/wps/contenthandler/gov/!ut/p/digest!g98GW7j82ZUibYO5KtEZaw/sp/mashup:ra:collection?soffset=0&amp;eoffset=5&amp;themeID=ZJ_O9LGHI40NG82E0QG0O0KF412S1&amp;locale=en&amp;mime-type=text%2Fcss&amp;lm=1662033487517&amp;entry=wp_toolbar_common__0.0%3Ahead_css&amp;entry=wp_portlet_css__0.0%3Ahead_css&amp;entry=wp_simple_contextmenu_css__0.0%3Ahead_css&amp;entry=wp_status_bar__0.0%3Ahead_css" rel="stylesheet" type="text/css"/><script type="text/javascript">(function(){if (typeof(wpModules) == 'undefined') wpModules = {}; if (typeof(wpModules.state) == 'undefined

In [61]:
# use soupstrainer
from bs4 import SoupStrainer
only_ul_tags = SoupStrainer('ul') 

In [66]:
# use beautiful soup to parse only ul tags
new_soup = BeautifulSoup(response.content, 'html.parser', parse_only=only_ul_tags).prettify()

In [76]:
# try one more time with lxml parser to use with etree
from xml.etree import ElementTree as ET

# create new soup
soup2 = BeautifulSoup(response.content, 'xml')
soup2.get_text()


'\n\n\n\n(function(){if (typeof(wpModules) == \'undefined\') wpModules = {}; if (typeof(wpModules.state) == \'undefined\') wpModules.state = {}; if (typeof(wpModules.state.page) == \'undefined\') wpModules.state.page = {};wpModules.state.page._initial=[{"nsuri":"http://www.ibm.com/xmlns/prod/websphere/portal/publicparams","name":"selection","value":["Z6_O06E1CC01PLL10QNTQPHP0Q741"]},{"nsuri":"http://www.ibm.com/xmlns/prod/websphere/portal/publicparams","name":"labelMappings","value":["Z6_O06E1CC01PLL10QNTQPHP0QOE3","Z6_O06E1CC01PLL10QNTQPHP0Q741","Z6_000000000000000000000000A0","Z6_O06E1CC01PLL10QNTQPHP0Q741"]},{"nsuri":"http://www.ibm.com/xmlns/prod/websphere/portal/publicparams","name":"path-info","value":["find-ohio-wineries","find-ohio-wineries"]},{"nsuri":"http://www.ibm.com/xmlns/prod/websphere/portal/publicparams","name":"expansions","value":["Z6_000000000000000000000000A0","Z6_O06E1CC01PLL10QNTQPHP0QOE3"]}];wpModules.state.page.selectionPath=[\'Z6_000000000000000000000000A0\',\

In [80]:
# try a different way
from urllib.request import urlopen

url = 'https://findohiowines.ohio.gov/discover/find-ohio-wineries/find-ohio-wineries'

page = urlopen(url)

html = page.read().decode('utf-8')

soup3 = BeautifulSoup(html, 'lxml')

In [81]:
print(str(soup3))

<!DOCTYPE html>
<html class="no-js" lang="en">
<head>
<meta charset="utf-8"/>
<!-- rel=dynamic-content indicates an element that is replaced with the contents produced by the specified href. 
	 dyn-cs:* URIs are resolved using the WP DynamicContentSpotMappings resource environment provider. These values can
	 also be set using theme metadata if a theme is specified in the URI (e.g. @tl:oid:theme_unique_name). ODX v1.02 -->
<link href="/wps/contenthandler/gov/!ut/p/digest!g98GW7j82ZUibYO5KtEZaw/sp/mashup:ra:collection?soffset=0&amp;eoffset=4&amp;themeID=ZJ_O9LGHI40NG82E0QG0O0KF412S1&amp;locale=en&amp;mime-type=text%2Fcss&amp;lm=1658014472884&amp;entry=wp_portlet_css__0.0%3Ahead_css&amp;entry=wp_simple_contextmenu_css__0.0%3Ahead_css&amp;entry=wp_status_bar__0.0%3Ahead_css" rel="stylesheet" type="text/css"/><script src="/wps/contenthandler/gov/!ut/p/digest!g98GW7j82ZUibYO5KtEZaw/mashup/ra:collection?themeID=ZJ_O9LGHI40NG82E0QG0O0KF412S1&amp;locale=en&amp;mime-type=text%2Fjavascript&amp;l

In [106]:
# Try selenium
from selenium import webdriver
from selenium.webdriver.chrome.options import Options
from selenium.webdriver.common.by import By


DRIVER_PATH = 'C:/Users/silva/AppData/Local/Temp/Temp1_chromedriver_win32.zip/chromedriver.exe'

options = Options()
options.headless = True
options.add_argument("--window-size=1920,1200")

driver = webdriver.Chrome(options=options, executable_path=DRIVER_PATH)

driver.get('https://findohiowines.ohio.gov/discover/find-ohio-wineries/find-ohio-wineries')



In [107]:
print(driver.page_source)

<html class="js cookies geolocation history no-ie8compat json queryselector svg cors cssescape supports target es5syntax es6array arrow es6collections promises filereader svgfilters audio video bgpositionshorthand multiplebgs csspointerevents cssremunit rgba preserve3d csscalc cubicbezierrange cssgradients opacity csspositionsticky csschunit cssexunit hsla no-touchevents checked displaytable display-table fontface generatedcontent no-hairline cssinvalid lastchild nthchild cssscrollbar siblinggeneral subpixelfont cssvalid cssvhunit cssvmaxunit cssvminunit cssvwunit mediaqueries textshadow requestanimationframe raf objectfit object-fit no-regions no-wrapflow cssanimations csspseudoanimations backgroundcliptext bgpositionxy bgrepeatround bgrepeatspace backgroundsize bgsizecover borderimage borderradius boxshadow boxsizing csscolumns csscolumns-width csscolumns-span csscolumns-fill csscolumns-gap csscolumns-rule csscolumns-rulecolor csscolumns-rulestyle csscolumns-rulewidth csscolumns-brea

In [119]:
location_elements = driver.find_elements(By.CLASS_NAME, 'odx-location js-location')
location_elements

[]

## Perusing the Ohio's Department Agriculture website, one of the major exports Ohio advertises are its wines.
